In [30]:
#!/usr/bin/env python
# coding: utf-8

# In[1]:


import torch
from torch import nn
from collections import OrderedDict
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt


# In[29]:


class CoDA_Regress(nn.Module):
    
    def __init__(self, input_dim, dimension, encoder_shape, decoder_shape):
        super(CoDA_Regress, self).__init__()
        
        #define regression layer
        self.linear = nn.Linear(dimension, 1)
        
        encoder_dict = OrderedDict()
        
        #first layer will be twice input size, since we are feeding in both c_kl and X 
        encoder_dict["layer0"] = nn.Linear(2 * input_dim, encoder_shape[0])

        for i in range(0,len(encoder_shape)-1):
            encoder_dict["layer"  + str(i)] = nn.Linear(encoder_shape[i], encoder_shape[i+1])
            encoder_dict["layer_ac"  + str(i)] = nn.ELU()
        encoder_dict["final_layer"] = nn.Linear(encoder_shape[-1], dimension)
        encoder_dict["final_ac"] = nn.ELU()


        self.encoder = nn.Sequential(encoder_dict)
        
        decoder_dict = OrderedDict()
        decoder_dict["layer0"] = nn.Linear(dimension, decoder_shape[0])

        for i in range(0,len(decoder_shape)-1):
            decoder_dict["layer"  + str(i)] = nn.Linear(decoder_shape[i], decoder_shape[i+1])
            decoder_dict["layer_ac"  + str(i)] = nn.ELU()

        #final layer will map back to input dim
        decoder_dict["final_layer"] = nn.Linear(decoder_shape[-1], input_dim)
        decoder_dict["final_ac"] = nn.ELU()

        self.decoder = nn.Sequential(decoder_dict)
        
        
    def forward(self,x):
        #run the encoding and store the low level representation as A
        x_ckl = torch.log(torch.clamp(check(x), 1e-8,1))
        
        #pass in both x and x_ckl as per paper
        self.A = self.encoder(torch.cat((x, x_ckl), 1))
        self.reconstruction = self.decoder(self.A)
        self.pred = self.linear(self.A)
        #return both the predicted target, and the reconstruction so both can be inputs to the combined loss
        return self.pred, self.reconstruction, x_ckl
        


# In[39]:


class Combined_Loss(torch.nn.Module):
    def __init__(self, lam):
        super(Combined_Loss,self).__init__()
        self.CoDA_Loss = CoDA_Loss()
        self.MSE = nn.MSELoss()
        self.lam = lam
        
    def forward(self,Y,X,y_hat,y):
        #X is original data, Y is CoDA reconstruction, y is targets, y_hat 
        #input needs to be normalised by g(x) (geometric mean) for X_hat
        #TODO centering matrix? Reduce mean? Mask for near zero values?  
        
        #extract reconstruction and original data from concatenation
        
        return self.MSE(y_hat, y) + self.lam * self.CoDA_Loss(Y,X)  

class CoDA_Loss(torch.nn.Module):
    
    def __init__(self):
        super(CoDA_Loss,self).__init__()
        
    def forward(self,Y,X):
        #X is original data, Y is CoDA reconstruction
        X_check = check(X)
        #print ("XXX", X_check)
        coda_loss = torch.sum(torch.exp(Y)) - torch.sum(X_check * Y)
        return coda_loss

def check(X):
    #assume input is tensor so we can use the numpy() method
    assert type(X) == torch.Tensor
    gmean = torch.prod(X, 1) ** (1./X.shape[1])
    return torch.div(X.t(),  torch.clamp(gmean, min=1e-8)).t()


# In[60]:


data = pd.read_csv("Data 18. Compositions and total pebble counts of 92 glacial tills.csv")




# headers = data[1]
# features = data[0][:,co_feature_indices]
# targets = data[0][:,target_index]
    
# #normalise the compositional features. TODO anything extra to deal with non compositional features?
# 


features = data[data.columns[1:-1]]
targets = data[data.columns[-1]]

features = np.array([feat/sum(feat) for feat in features.values])

features = torch.FloatTensor(features)
targets = torch.FloatTensor(targets)






In [32]:
# In[40]:


#training code stub, read in data as X and targets as y
#TODO substitute this into model class, and set up API similar to original CoDA-PCA paper
X = features
y = targets.reshape(-1,1)
model = CoDA_Regress(X.shape[1], 2, [100,], [3,])
#define the combined loss with hyperparameter lambda
l = 1
loss_function = Combined_Loss(l)
optim = torch.optim.SGD(model.parameters(), lr = 0.0001)
    
for epoch in range(0,1000):
    pred, recon, A = model.forward(torch.FloatTensor(X))
    loss = loss_function(recon, torch.FloatTensor(X), pred, torch.FloatTensor(y))
        
    optim.zero_grad()
        
    loss.backward()
    optim.step()
        
    epoch += 1
    
    if (epoch % 100 == 0):
        print("epoch {}, loss {}".format(epoch, loss))

    if (epoch == 1):
        print("A",A)


XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [2.5300e+07, 7.1100e+07, 3.6000e+06, 0.0000e+00],
        [3

        [3.1400e+07, 6.5900e+07, 2.7000e+06, 0.0000e+00]])
XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [

XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [2.5300e+07, 7.1100e+07, 3.6000e+06, 0.0000e+00],
        [3

XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [2.5300e+07, 7.1100e+07, 3.6000e+06, 0.0000e+00],
        [3

XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [2.5300e+07, 7.1100e+07, 3.6000e+06, 0.0000e+00],
        [3

...

XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [2.5300e+07, 7.1100e+07, 3.6000e+06, 0.0000e+00],
        [3

        [3.1400e+07, 6.5900e+07, 2.7000e+06, 0.0000e+00]])
XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [

        [3.1400e+07, 6.5900e+07, 2.7000e+06, 0.0000e+00]])
XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [

        [3.1400e+07, 6.5900e+07, 2.7000e+06, 0.0000e+00]])
XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [

XXX tensor([[9.1800e+07, 7.1000e+06, 1.1000e+06, 0.0000e+00],
        [2.2967e+01, 2.6093e+00, 1.2918e-01, 1.2918e-01],
        [1.6620e+01, 2.0751e+00, 1.5230e-01, 1.9038e-01],
        [8.4600e+07, 1.3500e+07, 0.0000e+00, 1.9000e+06],
        [2.4540e+00, 1.3539e+01, 5.0082e-02, 6.0098e-01],
        [1.9805e+00, 1.9323e+00, 2.1411e-01, 1.2204e+00],
        [3.4300e+07, 5.9800e+07, 5.9000e+06, 0.0000e+00],
        [3.2152e+00, 1.1216e+01, 5.9818e-02, 4.6359e-01],
        [1.3387e+01, 6.2750e+00, 5.9761e-02, 1.9920e-01],
        [6.1188e+00, 5.7509e+00, 8.5835e-02, 3.3108e-01],
        [3.3691e+00, 1.4287e+01, 7.2067e-02, 2.8827e-01],
        [1.1311e+07, 8.8288e+07, 4.0040e+05, 0.0000e+00],
        [2.5129e+01, 2.1792e+00, 2.2067e-01, 8.2753e-02],
        [8.1618e+07, 1.7582e+07, 0.0000e+00, 7.9920e+05],
        [9.7698e+07, 2.3023e+06, 0.0000e+00, 0.0000e+00],
        [1.0082e+00, 2.8200e+01, 1.1861e-01, 2.9653e-01],
        [2.5300e+07, 7.1100e+07, 3.6000e+06, 0.0000e+00],
        [3